## **Step4: Most Informative Words**

### 1. **For LLM**
- Used Shap tool
- We can see the review given by the user
- The predicted review by the LLM
- And the most important words

In [1]:
import pandas as pd
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch
import shap
import matplotlib.pyplot as plt

In [2]:
# Load tokenized dataset
df = pd.read_csv('goodreads_15k_english_tokenized_filtered.csv')
sample_reviews = df[['review_text', 'rating']][10:30]

In [3]:
model_path = "./fine_tuned_model_optuna"
model = AutoModelForSequenceClassification.from_pretrained(model_path).to("cuda")
tokenizer = AutoTokenizer.from_pretrained(model_path)

In [4]:
# Truncate reviews to a maximum of 512 tokens if they exceed this limit
max_length = 512
truncated_reviews = []

#for review in sample_reviews:
for review in sample_reviews['review_text']:
    tokens = tokenizer.encode(review, truncation=True, max_length=max_length)
    truncated_text = tokenizer.decode(tokens, skip_special_tokens=True)
    truncated_reviews.append(truncated_text)

In [5]:
def model_predict(texts):
    if isinstance(texts, (str, list)):
        if isinstance(texts, str):
            texts = [texts]  # Convert single string to a list of one element
    else:
        texts = [str(text) for text in texts]  # Ensure each element is converted to a string if possible

    inputs = tokenizer(texts, padding=True, truncation=True, max_length=max_length, return_tensors="pt").to("cuda")
    with torch.no_grad():
        output = model(**inputs)
    return output.logits.cpu().numpy()

In [6]:
# Create the SHAP explainer
masker = shap.maskers.Text(tokenizer)  # Define how to mask the text
explainer = shap.Explainer(model_predict, masker)

# Calculate SHAP values for the truncated reviews
shap_values = explainer(truncated_reviews)

for i in range(len(truncated_reviews)):
    # Get the actual rating and predicted rating
    actual_rating = sample_reviews['rating'].iloc[i]
    predicted_rating = model_predict([truncated_reviews[i]])[0][0]  # Assuming ratings are 1-indexed
    
    print(f"Rating given by user: {actual_rating}")
    print(f"Predicted Rating by model: {predicted_rating}")
    print(f"Explanation for Review {i + 1}:")
    shap.text_plot(shap_values[i])

PartitionExplainer explainer:  65%|██████▌   | 13/20 [00:22<00:05,  1.25it/s]

  0%|          | 0/498 [00:00<?, ?it/s]

PartitionExplainer explainer: 21it [00:48,  2.69s/it]                        

Rating given by user: 5
Predicted Rating by model: 4.91116189956665
Explanation for Review 1:


Rating given by user: 4
Predicted Rating by model: 4.093384265899658
Explanation for Review 2:


...

Rating given by user: 5
Predicted Rating by model: 4.698384761810303
Explanation for Review 16:


Rating given by user: 3
Predicted Rating by model: 3.920062780380249
Explanation for Review 17:


Rating given by user: 3
Predicted Rating by model: 3.458266496658325
Explanation for Review 18:


Rating given by user: 4
Predicted Rating by model: 4.3867316246032715
Explanation for Review 19:


Rating given by user: 4
Predicted Rating by model: 4.0084309577941895
Explanation for Review 20:


### **It is interesting to see how words affect the prediction of the LLM. For example in the "Explanation for Review 10:" we can see that the most important words are "engaging, very", thus making the model predict a high rating.**

### 2. **For Classification Methods (step3)**
- Results are shown in the step3.ipynb
- For each genre we can see the most important words that lead to its detection